In [1]:
import datetime 

import sys
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import bokeh
import folium 
import geopandas as gpd 
current_file_path = os.path.abspath(os.getcwd())
parent_dir = os.path.abspath(os.path.join(current_file_path, '..','..','..'))
if parent_dir not in sys.path:
    sys.path.insert(0, parent_dir)

from constants.paths import FOLDER_PATH
from load_inputs.systematic_analysis.load_netmob import load_dataset,get_list_apps,get_list_days,get_DL_UL_paths,read_csv,load_netmob_gdf
from load_inputs.systematic_analysis.utils import get_histogram_per_day_type,get_boxplot_per_spatial_unit_per_day_type,heatmap
from load_inputs.systematic_analysis.utils import IN_bdc,OUT_bdc,IN_nbdc,OUT_nbdc

folder_path = f'{FOLDER_PATH}/../raw_data/NetMob/'
shp_iris_path = f'{FOLDER_PATH}/../raw_data/lyon_iris_shapefile/'
path_save = '../../../../../../data/NetMob/NetMob_Lyon'
folder_path = '../../../../../../data/NetMob/NetMob_raw'

/root/anaconda3/envs/pytorch-2.0.1/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


No module xgboost
Training and Hyper-parameter tuning with Ray is not possible


# Load Spatial Dataset

In [2]:
Netmob_gdf_joined,working_zones,n_rows,n_cols = load_netmob_gdf(folder_path,shp_iris_path)
Netmob_gdf_joined = Netmob_gdf_joined.drop_duplicates('tile_id')
Netmob_gdf_joined = Netmob_gdf_joined[['tile_id','INSEE_COM','NOM_COM','NOM_IRIS','geometry']]
Netmob_gdf_joined = gpd.GeoDataFrame(Netmob_gdf_joined,crs='EPSG:4326') #Don't know why, but the geodataframe seem corrupted as we can't convert it into GeoJson, that's why we need to use "gpd.GeoDataFrame()"
Netmob_gdf_joined
Netmob_gdf_joined.head()

tile_id  INSEE_COM            NOM_COM         NOM_IRIS  \
5067    34807    69204.0  Saint-Genis-Laval  Basses Barolles   
5194    35094    69204.0  Saint-Genis-Laval  Basses Barolles   
5195    35095    69204.0  Saint-Genis-Laval  Basses Barolles   
5196    35096    69204.0  Saint-Genis-Laval  Basses Barolles   
5328    35380    69204.0  Saint-Genis-Laval  Basses Barolles   

                                               geometry  
5067  POLYGON ((4.78896 45.66473, 4.78900 45.66563, ...  
5194  POLYGON ((4.78900 45.66563, 4.78904 45.66653, ...  
5195  POLYGON ((4.79028 45.66560, 4.79032 45.66650, ...  
5196  POLYGON ((4.79156 45.66557, 4.79160 45.66647, ...  
5328  POLYGON ((4.78776 45.66656, 4.78780 45.66745, ...

# Load Raw data:

In [3]:
""" Choices: 

['Apple_Video', 'Google_Play_Store', 'Google_Maps', 'Web_Clothes', 'Uber', 'Twitter', 'Microsoft_Mail', 'Microsoft_Store', 'Apple_Music', 'Microsoft_Office', 'Pokemon_GO', 'Clash_of_Clans', 'Yahoo_Mail', 'PlayStation', 'Wikipedia', 'Apple_Web_Services', 'Pinterest', 'Web_Ads', 'Google_Mail', 'Google_Meet', 'Apple_Siri', 'Web_Adult', 'Spotify', 'Deezer', 'Waze', 'Web_Games', 'Apple_App_Store', 'Microsoft_Skydrive', 'Google_Docs', 'Microsoft_Web_Services', 'Molotov', 'YouTube', 'Apple_iTunes', 'Apple_iMessage', 'DailyMotion', 'Netflix', 'Web_Transportation', 'Web_Downloads', 'SoundCloud', 'TeamViewer', 'Google_Web_Services', 'Facebook', 'EA_Games', 'Tor', 'Amazon_Web_Services', 'Web_e-Commerce', 'Telegram', 'Apple_Mail', 'Dropbox', 'Web_Food', 'Apple_iCloud', 'Skype', 'Facebook_Messenger', 'Twitch', 'Microsoft_Azure', 'Instagram', 'Facebook_Live', 'Web_Streaming', 'Orange_TV', 'Periscope', 'Snapchat', 'Web_Finance', 'WhatsApp', 'Web_Weather', 'Google_Drive', 'LinkedIn', 'Yahoo', 'Fortnite']
"""

app = 'Instagram' # 'Deezer' # 'Spotify' # 'Web_Weather' # 'Instagram' # 'Google_Maps' # 'WhatsApp' 

# Load Datasets:
data = np.load(f'{path_save}/{app}.npy')
idx = pd.read_pickle(f'{path_save}/index.pkl')
cols = pd.read_pickle(f'{path_save}/columns.pkl')

df_loaded = pd.DataFrame(data, index=idx, columns=cols)
df_loaded.shape

(7392, 27446)

## HeatMap:

In [4]:
import folium
from folium.plugins import HeatMap
from folium.plugins import HeatMapWithTime
from load_inputs.systematic_analysis.utils import preprocess_df

filter_q = 0.99 # None

# # Night time: 
# start = datetime.time(23,0,0)
# end = datetime.time(6,0,0)
# period = None

# # Evening Peak :
# period = 'evening_peak'   # 'all_day','morning_peak','evening_peak' # None
# start = None
# end = None

# All day & Business day:
period = 'all_day'
start = None
end = None

city = 'Lyon'
df = df_loaded.copy()


# filter quantile: 
if period is None: 
   df = preprocess_df(df,filter_q = filter_q,city=city,start=start,end=end)
else:
   df_bd_in, df_nbd_in = preprocess_df(df,period=period,city= city,filter_q = filter_q,start=start,end=end)
   df = pd.concat([df_bd_in,df_nbd_in])

print('Remaining shape: ',df.shape)


ts = df.sum(0)

df_map = Netmob_gdf_joined.merge(ts.rename('volume'), on='tile_id').to_crs(epsg=4326)



Number of remaining time-slots after filtering 4896
Number of remaining time-slots after filtering 2496
Remaining shape:  (7392, 27446)


In [5]:
centroids = df_map.geometry.centroid
heat_data = [[point.y, point.x, vol] for point, vol in zip(centroids, df_map['volume'])]
m = folium.Map(location=[centroids.y.mean(), centroids.x.mean()], zoom_start=11,tiles = 'CartoDB positron')
HeatMap(
    heat_data,
    radius=8,
    blur=20,
    min_opacity=0,
    gradient={0.4: 'blue', 0.5: 'lime', 0.7: 'yellow', 1: 'red'}
).add_to(m)
m

/tmp/ipykernel_264263/3725768165.py:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroids = df_map.geometry.centroid


# HeatMap With Time:

In [47]:
tile_id_order = list(Netmob_gdf_joined.tile_id.values)
centroids = Netmob_gdf_joined.geometry.centroid

# clipping to quantile 0.99
df_copy = df[tile_id_order].copy()
df_copy = df_copy.clip(upper=df_copy.quantile(0.99).values,axis=1)
resampled_df = df_copy.groupby([df_copy.index.hour, df_copy.index.minute]).sum()
resampled_df.index = [datetime.datetime(2019,1,1,hour=hour,minute=minute) for hour,minute in resampled_df.index]

# Select time range:
start = datetime.datetime(2019,1,1,6,30) # datetime.datetime(2019,1,1,0,0)
end = datetime.datetime(2019,1,1,7,30) # datetime.datetime(2019,1,1,23,59)
resampled_df = resampled_df[(resampled_df.index >= start) & (resampled_df.index <= end)]

# Normalize ?
maxi = resampled_df.max().max()
resampled_df = resampled_df / maxi
# Set point < threshold to 0
threshold = 0.01
resampled_df = resampled_df.mask(resampled_df < threshold, 0)
resampled_df = resampled_df*100  # Scale to [0,100] for better visualization

heatmap_index = resampled_df.index
heatmap_index = [f"{hour}:{minute}" for hour,minute in zip(resampled_df.index.hour,resampled_df.index.minute)]  # Label and not timestamp


# L_heat_data  = [[[point.y, point.x, vol] for point, vol in zip(centroids, resampled_df.iloc[i].values)] for i in range(resampled_df.shape[0])]
# Opitmized way: 
coords = np.array([[p.y, p.x] for p in centroids])
L_heat_data = [np.column_stack((coords[row > 0], row[row > 0])).tolist() for row in resampled_df.values]



/tmp/ipykernel_264263/750315139.py:2: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroids = Netmob_gdf_joined.geometry.centroid


In [55]:
m = folium.Map(location=[centroids.y.mean(), centroids.x.mean()], zoom_start=11,tiles = 'CartoDB positron')
HeatMapWithTime(
    L_heat_data,
    index=heatmap_index,
    max_opacity=0.7,
    radius=12,
    blur=15,
    gradient={0.01: 'blue', 0.2: 'lime', 0.4: 'yellow', 1: 'red'}
).add_to(m)
m

In [51]:
# Diagnostic des données avant l'affichage de la carte
print(f"Nombre de lignes dans resampled_df : {len(resampled_df)}")
print(f"Valeur maximale dans resampled_df : {resampled_df.values.max() if not resampled_df.empty else 'DataFrame vide'}")
print(f"Présence de valeurs NaN : {resampled_df.isna().any().any()}")
print(f"Nombre de pas de temps dans L_heat_data : {len(L_heat_data)}")
if len(L_heat_data) > 0:
    print(f"Nombre de points pour le premier pas de temps : {len(L_heat_data[0])}")
    if len(L_heat_data[0]) > 0:
        print(f"Structure d'un point (lat, lon, poids) : {L_heat_data[0][0]}")
        print(f"Types des données du point : {[type(x) for x in L_heat_data[0][0]]}")
print(f"Centre de la carte : Lat {centroids.y.mean()}, Lon {centroids.x.mean()}")


# Diagnostic de l'index et de la densité des données
print(f"Type de l'index : {type(resampled_df.index)}")
print(f"Exemple de label dans heatmap_index : '{heatmap_index[0]}'")
print(f"Nombre total de points à traiter : {sum(len(step) for step in L_heat_data)}")

# Test de réduction drastique pour isoler un problème de performance
# On ne garde que les 100 premiers points du premier pas de temps
L_heat_data_test = [step[:100] for step in L_heat_data]
print(f"Volume réduit pour test : {len(L_heat_data_test[0])} points")

# Vérification de l'amplitude des poids après filtrage
all_weights = [p[2] for step in L_heat_data for p in step]
if all_weights:
    print(f"Poids minimal : {min(all_weights)}, Poids maximal : {max(all_weights)}")

Nombre de lignes dans resampled_df : 5
Valeur maximale dans resampled_df : 100.0
Présence de valeurs NaN : False
Nombre de pas de temps dans L_heat_data : 5
Nombre de points pour le premier pas de temps : 18826
Structure d'un point (lat, lon, poids) : [45.666063446445406, 4.789660496308202, 1.1226674243777583]
Types des données du point : [<class 'float'>, <class 'float'>, <class 'float'>]
Centre de la carte : Lat 45.76038561637581, Lon 4.866161813352021
Type de l'index : <class 'pandas.core.indexes.datetimes.DatetimeIndex'>
Exemple de label dans heatmap_index : '6:30'
Nombre total de points à traiter : 115581
Volume réduit pour test : 100 points
Poids minimal : 1.0001026807738373, Poids maximal : 100.0


In [54]:
heatmap_index = [t.strftime('%H:%M') for t in resampled_df.index]

# Préparation des données avec conversion en types natifs et filtrage de densité
L_heat_data = []
max_intensity = float(resampled_df.values.max())

for row in resampled_df.values:
    # Filtrage des points de faible intensité pour alléger le rendu (top 20% ou > threshold)
    mask = row > (max_intensity * 0.05)
    step_coords = coords[mask]
    step_weights = row[mask]
    
    # Construction de la liste avec conversion explicite en float
    step_data = np.column_stack((step_coords, step_weights)).astype(float).tolist()
    L_heat_data.append(step_data)

# Création de la carte avec paramètres de rendu explicites
m = folium.Map(location=[45.76, 4.86], zoom_start=11, tiles='CartoDB positron')

HeatMapWithTime(
    L_heat_data,
    index=heatmap_index,
    radius=12,
    blur=15,
    auto_play=True,
    max_opacity=0.8,
    gradient={0.1: 'blue', 0.4: 'lime', 0.7: 'yellow', 1: 'red'}
).add_to(m)
m

## Load data aggregated by tags (ex: IRIS)


NetMob_selected_apps= ['Google_Maps'] 
NetMob_transfer_mode = ['DL'] 
NetMob_selected_tags = ['iris']
NetMob_expanded = ''
NetMob_only_epsilon = False
city = 'Lyon'
signal = 'netmob_POIs'
ds, df_raw, df = load_dataset(signal,
            NetMob_selected_apps,
            NetMob_transfer_mode,
            NetMob_selected_tags,
            NetMob_expanded,
            NetMob_only_epsilon,
            )
df_raw.columns.name = 'Spatial Unit ID'
df_raw.head()